In [10]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px

In [11]:
# read dataframe

df = pd.read_csv('time_series_30min_singleindex.csv')
df['utc_timestamp'] = pd.to_datetime(df['utc_timestamp'])
print(df.columns)
time_load_df = df[['utc_timestamp', 'GB_NIR_load_actual_entsoe_transparency']]

Index(['utc_timestamp', 'cet_cest_timestamp',
       'CY_load_actual_entsoe_transparency',
       'CY_load_forecast_entsoe_transparency',
       'CY_wind_onshore_generation_actual',
       'GB_GBN_load_actual_entsoe_transparency',
       'GB_GBN_load_forecast_entsoe_transparency', 'GB_GBN_solar_capacity',
       'GB_GBN_solar_generation_actual', 'GB_GBN_solar_profile',
       'GB_GBN_wind_capacity', 'GB_GBN_wind_generation_actual',
       'GB_GBN_wind_profile', 'GB_GBN_wind_offshore_capacity',
       'GB_GBN_wind_offshore_generation_actual',
       'GB_GBN_wind_offshore_profile', 'GB_GBN_wind_onshore_capacity',
       'GB_GBN_wind_onshore_generation_actual', 'GB_GBN_wind_onshore_profile',
       'GB_NIR_load_actual_entsoe_transparency',
       'GB_NIR_load_forecast_entsoe_transparency', 'GB_NIR_solar_capacity',
       'GB_NIR_wind_onshore_capacity', 'GB_NIR_wind_onshore_generation_actual',
       'GB_UKM_load_actual_entsoe_transparency',
       'GB_UKM_load_forecast_entsoe_transparency

In [12]:
time_load_df = time_load_df.dropna()
time_load_df.reset_index(drop=True, inplace=True)
time_load_df.head(10)

utc_timestamp  GB_NIR_load_actual_entsoe_transparency
0 2015-01-01 00:30:00+00:00                                   849.0
1 2015-01-01 01:00:00+00:00                                   797.0
2 2015-01-01 01:30:00+00:00                                   768.0
3 2015-01-01 02:00:00+00:00                                   745.0
4 2015-01-01 02:30:00+00:00                                   732.0
5 2015-01-01 03:00:00+00:00                                   697.0
6 2015-01-01 03:30:00+00:00                                   683.0
7 2015-01-01 04:00:00+00:00                                   654.0
8 2015-01-01 04:30:00+00:00                                   634.0
9 2015-01-01 05:00:00+00:00                                   614.0

In [13]:
px.line(time_load_df, x='utc_timestamp', y='GB_NIR_load_actual_entsoe_transparency', title='Load in Cyprus')


In [14]:
time_load_df.columns = ['time', 'value']

In [15]:
from TimeseriesDatasets import TimeseriesOverlapDataset, TimeseriesRollingDataset

# split into train for 2015-2018, val for 2018-01 to 2018-6, test for 2018-07 to 2018-12

train_df = time_load_df.loc[time_load_df['time'] < '2019-01-01']
val_df = time_load_df.loc[(time_load_df['time'] >= '2019-01-01') & (time_load_df['time'] < '2020-01-01')]
test_df = time_load_df.loc[time_load_df['time'] >= '2020-01-01']

trainds = TimeseriesRollingDataset(train_df, 24*7*2)
valds = TimeseriesRollingDataset(val_df, 24*7*2)
testds = TimeseriesRollingDataset(test_df, 24*7*2)

print(len(trainds), len(valds), len(testds))

                       time     value  year  month  weekday  day  hour  minute
0 2015-01-01 00:30:00+00:00 -0.408238  2015      1        3    1     0      30
1 2015-01-01 01:00:00+00:00 -0.623878  2015      1        3    1     1       0
2 2015-01-01 01:30:00+00:00 -0.744139  2015      1        3    1     1      30
3 2015-01-01 02:00:00+00:00 -0.839519  2015      1        3    1     2       0
4 2015-01-01 02:30:00+00:00 -0.893429  2015      1        3    1     2      30
                           time     value  year  month  weekday  day  hour  \
69815 2019-01-01 00:00:00+00:00 -0.620208  2019      1        1    1     0   
69816 2019-01-01 00:30:00+00:00 -0.758712  2019      1        1    1     0   
69817 2019-01-01 01:00:00+00:00 -0.918856  2019      1        1    1     1   
69818 2019-01-01 01:30:00+00:00 -1.018405  2019      1        1    1     1   
69819 2019-01-01 02:00:00+00:00 -1.135268  2019      1        1    1     2   

       minute  
69815       0  
69816      30  
69817    

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:54: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:55: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:56: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [16]:
from WavenetT2V import Wavenet_t2v

wavenet = Wavenet_t2v(6, 31, 3, config = [32, 63, 64, 128, 64], dilatation_rates = [0, 12, 8, 4, 2], outsize = 1)



In [17]:
from tester import ForecastTester

tester = ForecastTester([wavenet], trainds, valds, testds)

In [18]:
tester.train()

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\accelerator_connector.py:447: LightningDeprecationWarning:

Setting `Trainer(gpus=1)` is deprecated in v1.7 and will be removed in v2.0. Please use `Trainer(accelerator='gpu', devices=1)` instead.

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name     | Type       | Params
----------------------------------------
0 | blocks   | ModuleList | 0     
1 | time_emb | t2v        | 217   
2 | wavenet  | WaveNet    | 1.1 M 
----------------------------------------
1.1 M     Trainable params
0         Non-trainable params
1.1 M     Total params
4.430     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:236: PossibleUserWarning:

The dataloader, val_dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:236: PossibleUserWarning:

The dataloader, train_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.

c:\Python\lib\site-packages\pytorch_lightning\trainer\trainer.py:1892: PossibleUserWarning:

The number of training batches (7) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training e

Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

`Trainer.fit` stopped: `max_epochs=10` reached.


In [40]:
import pytorch_lightning as pl

model = tester.testers[0].model
test_loader = tester.testers[0].testdl

preds = []
ys = []

for x, t, y in test_loader:
    print(x.shape, t.shape, y.shape)
    pred = model(x, t)
    preds.append(pred.detach().numpy())
    ys.append(y.detach().numpy())



torch.Size([32, 336, 1]) torch.Size([32, 336, 6]) torch.Size([32, 336, 1])
torch.Size([7, 336, 1]) torch.Size([7, 336, 6]) torch.Size([7, 336, 1])


In [41]:
preds = np.concatenate(preds)
ys = np.concatenate(ys)

preds.shape, ys.shape

((39, 336, 1), (39, 336, 1))

In [42]:
preds = preds.reshape(-1)
ys = ys.reshape(-1)

In [56]:
print(test_df['time'].values[:13104].shape, preds.shape, ys.shape)
predsdf = pd.DataFrame({'time':test_df['time'].values[:13104], 'pred': preds, 'y': ys})

(13104,) (13104,) (13104,)


In [57]:
predsdf.head(10)

time      pred         y
0 2020-01-01 00:00:00 -0.050761 -0.062626
1 2020-01-01 00:30:00 -0.242600 -0.200292
2 2020-01-01 01:00:00 -0.410946 -0.420559
3 2020-01-01 01:30:00 -0.523042 -0.507748
4 2020-01-01 02:00:00 -0.575774 -0.576581
5 2020-01-01 02:30:00 -0.628001 -0.594937
6 2020-01-01 03:00:00 -0.732364 -0.723425
7 2020-01-01 03:30:00 -0.855580 -0.856503
8 2020-01-01 04:00:00 -0.974430 -0.975814
9 2020-01-01 04:30:00 -1.065733 -1.072181

In [58]:
px.line(predsdf, x='time', y=['pred', 'y'], title='Load in Cyprus')

In [59]:
# r2 score, mae, mse, rmse

from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error

r2_score(predsdf['y'], predsdf['pred']), mean_absolute_error(predsdf['y'], predsdf['pred']), mean_squared_error(predsdf['y'], predsdf['pred']), np.sqrt(mean_squared_error(predsdf['y'], predsdf['pred']))

(0.9984504457047597, 0.028016841, 0.0015484559, 0.039350424)